In [48]:
import pandas as pd
import nltk
import numpy as np
import csv
import torch
import torch.optim as optim
import torch.nn as nn
import torch.nn.functional as F
from torchtext.data import Field
from torchtext.data import TabularDataset
from torchtext.data import Iterator, BucketIterator
from sklearn.metrics import confusion_matrix

In [49]:
tokenize = lambda x: x.split()
TEXT = Field(sequential=True, tokenize=tokenize, lower=True, fix_length=100)
LABEL = Field(sequential=False, use_vocab=False)

In [50]:
train_stances = pd.read_csv("fn_data/train_stances.csv")
train_bodies = pd.read_csv("fn_data/train_bodies.csv")

In [51]:
train = pd.read_csv("lstmstuff/train_data_consolidated.csv")
val = pd.read_csv("lstmstuff/val_data_consolidated.csv")

In [52]:
train_datafields = [("Body ID", None),
                 ("Headline", TEXT),
                    ("Body", TEXT),
                 ("Stance", LABEL)]

trn, vld = TabularDataset.splits(
               path="",
               train='train_data_related_only_12_2.csv', validation="val_data_related_only_12_2.csv",
               format='csv',
               skip_header=True,
               fields=train_datafields)

In [53]:
TEXT.build_vocab(trn, vectors = 'glove.6B.100d')

In [54]:
train_iter, val_iter = BucketIterator.splits(
 (trn, vld),
 batch_sizes=(128,128),
 sort_key=lambda x: len(x.Body), # the BucketIterator needs to be told what function it should use to group the data.
 sort_within_batch=False,
 repeat=False
)

In [55]:
class BatchGenerator:
    def __init__(self, dl, x_field1, x_field2, y_field):
        self.dl, self.x_field1, self.x_field2, self.y_field = dl, x_field1, x_field2, y_field
        
    def __len__(self):
        return len(self.dl)
    
    def __iter__(self):
        for batch in self.dl:
            X1 = getattr(batch, self.x_field1)
            X2 = getattr(batch, self.x_field2)
            y = getattr(batch, self.y_field)
            yield (X1, X2, y)
            
train_batch_it = BatchGenerator(train_iter, 'Body','Headline', 'Stance')
val_batch_it = BatchGenerator(val_iter, 'Body', 'Headline', 'Stance')

In [64]:
# class RNN(nn.Module):
#     def __init__(self, input_dim, embedding_dim, hidden_dim, output_dim):
#         super().__init__()
        
#         self.embedding = nn.Embedding(input_dim, embedding_dim)
#         self.lstm_headline = nn.LSTM(embedding_dim, hidden_dim)
#         self.lstm_article = nn.LSTM(embedding_dim, hidden_dim)
#         self.fc = nn.Linear(hidden_dim, output_dim)
        
#     def forward(self, x):

#         #x = [sent len, batch size]
        
#         embedded = self.embedding(x)
        
#         #embedded = [sent len, batch size, emb dim]
        
#         output, hidden = self.rnn(embedded)
        
#         #output = [sent len, batch size, hid dim]
#         #hidden = [1, batch size, hid dim]
        
#         assert torch.equal(output[-1,:,:], hidden.squeeze(0))
        
#         return self.fc(hidden.squeeze(0))

import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable
class LSTMClassifier(nn.Module):

    def __init__(self, embedding_dim, hidden_dim, vocab_size, output_dim, batch_size):
        super(LSTMClassifier, self).__init__()
        self.hidden_dim = hidden_dim
        self.embed = nn.Embedding(vocab_size, embedding_dim)
        self.lstm_headline = nn.LSTM(embedding_dim, hidden_dim, bidirectional=True, dropout = 0.25, num_layers = 2)
        self.lstm_article = nn.LSTM(embedding_dim, hidden_dim, bidirectional=True, dropout = 0.2, num_layers = 2)
        self.fc = nn.Linear(hidden_dim*2, output_dim*8)
        self.fc2 = nn.Linear(output_dim*8, output_dim)
        self.batch_size = batch_size
        self.hidden1 = None
        self.hidden2 = None
        
    def init_hidden(self, batch_size):
        h0 = Variable(torch.zeros(4, batch_size, self.hidden_dim))
        c0 = Variable(torch.zeros(4, batch_size, self.hidden_dim))
        return (h0, c0)
    
    def forward(self, headline, article):
        headline_emb = self.embed(headline)
        ""
        article_emb = self.embed(article)
        
        lstm_headline_out, hidden = self.lstm_headline(headline_emb, self.hidden1)
        
        sum_padded_out_lstm1 = 0
        for tensor in torch.split(lstm_headline_out, self.hidden_dim, dim=2):
            sum_padded_out_lstm1 += tensor

        lstm_article_out, hidden2 = self.lstm_article(article_emb, hidden)
        res = self.fc(torch.cat((lstm_article_out[-1, :, :self.hidden_dim], lstm_article_out[0, :, self.hidden_dim:]), 1))
        res2 = self.fc2(F.relu(res))
        return res2
        

In [65]:
model = LSTMClassifier(100, 64, len(TEXT.vocab), 3, 128)

In [70]:
optimizer = optim.Adam(model.parameters())
criterion = nn.CrossEntropyLoss()

In [71]:
counter = []
loss_history = [] 
iteration_number= 0

model.train()
# Train the model
for epoch in range(0,10):
    for i, data in enumerate(train_batch_it,0):
        img0, img1 , label = data
        print("inputs are")
        print(img0.shape)
        print(img1.shape)
        optimizer.zero_grad()
        _, batch_size = img0.shape
        model.hidden1 = model.init_hidden(batch_size)
        model.hidden2 = model.init_hidden(batch_size)
        output = model(img0,img1)
        print("OUTPUT")
        print(output)
        print(label)
        loss = criterion(output.squeeze(),label.squeeze().long())
        loss.backward()
        optimizer.step()
        if True:
            print("Epoch number {}\n Current loss {}\n".format(epoch,loss.item()))
            iteration_number +=10
            counter.append(iteration_number)
            loss_history.append(loss.item())


inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[-0.0256,  0.1915,  0.0020],
        [-0.0382,  0.1906,  0.0050],
        [-0.0226,  0.1740, -0.0197],
        [-0.0296,  0.1906, -0.0086],
        [-0.0288,  0.1852, -0.0000],
        [-0.0232,  0.1704, -0.0117],
        [-0.0315,  0.1815, -0.0138],
        [-0.0270,  0.1762, -0.0178],
        [-0.0331,  0.2013,  0.0110],
        [-0.0165,  0.1962, -0.0109],
        [-0.0233,  0.1875, -0.0089],
        [-0.0191,  0.1975, -0.0089],
        [-0.0363,  0.1940, -0.0126],
        [-0.0211,  0.1942,  0.0033],
        [-0.0264,  0.1902, -0.0039],
        [-0.0205,  0.1870,  0.0049],
        [-0.0273,  0.1964, -0.0087],
        [-0.0235,  0.1866, -0.0080],
        [-0.0256,  0.1871, -0.0045],
        [-0.0335,  0.1980,  0.0060],
        [-0.0311,  0.1768,  0.0104],
        [-0.0277,  0.1891, -0.0161],
        [-0.0420,  0.1866,  0.0035],
        [-0.0437,  0.1934,  0.0064],
        [-0.0334,  0.1734, -0.0008],
        [-0

Epoch number 0
 Current loss 1.0339120626449585

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[-0.0707,  0.2440,  0.0424],
        [-0.0626,  0.2392,  0.0364],
        [-0.0649,  0.2439,  0.0383],
        [-0.0783,  0.2349,  0.0401],
        [-0.0846,  0.2228,  0.0536],
        [-0.0459,  0.2481,  0.0245],
        [-0.0580,  0.2280,  0.0313],
        [-0.0593,  0.2413,  0.0327],
        [-0.0720,  0.2390,  0.0258],
        [-0.0700,  0.2290,  0.0345],
        [-0.0515,  0.2421,  0.0218],
        [-0.0692,  0.2247,  0.0312],
        [-0.0662,  0.2307,  0.0182],
        [-0.0528,  0.2178,  0.0195],
        [-0.0556,  0.2382,  0.0302],
        [-0.0765,  0.2275,  0.0314],
        [-0.0670,  0.2353,  0.0346],
        [-0.0535,  0.2292,  0.0224],
        [-0.0575,  0.2278,  0.0133],
        [-0.0603,  0.2295,  0.0269],
        [-0.0631,  0.2342,  0.0340],
        [-0.0615,  0.2333,  0.0268],
        [-0.0622,  0.2321,  0.0269],
        [-0.0520,  0.2217,  0.0216],

Epoch number 0
 Current loss 0.9965620636940002

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[-0.1190,  0.2847,  0.0765],
        [-0.1102,  0.2777,  0.0731],
        [-0.1033,  0.2910,  0.0462],
        [-0.1207,  0.2989,  0.0762],
        [-0.1113,  0.3230,  0.0828],
        [-0.1138,  0.2903,  0.0745],
        [-0.1068,  0.2929,  0.0754],
        [-0.1037,  0.2911,  0.0702],
        [-0.1178,  0.2999,  0.0704],
        [-0.1213,  0.2931,  0.0639],
        [-0.1032,  0.2941,  0.0636],
        [-0.1066,  0.2974,  0.0607],
        [-0.1124,  0.2777,  0.0572],
        [-0.0957,  0.2858,  0.0635],
        [-0.1285,  0.2895,  0.0824],
        [-0.1143,  0.2934,  0.0559],
        [-0.1067,  0.2918,  0.0617],
        [-0.1191,  0.2880,  0.0776],
        [-0.1087,  0.2842,  0.0793],
        [-0.1205,  0.2658,  0.0642],
        [-0.0997,  0.3130,  0.0685],
        [-0.1197,  0.3057,  0.0730],
        [-0.1014,  0.3021,  0.0524],
        [-0.1145,  0.2839,  0.0740],

Epoch number 0
 Current loss 0.9758898615837097

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[-0.1709,  0.3941,  0.1166],
        [-0.1600,  0.3731,  0.0954],
        [-0.1702,  0.3706,  0.1195],
        [-0.1716,  0.3850,  0.1030],
        [-0.1698,  0.3522,  0.1005],
        [-0.1660,  0.3693,  0.1159],
        [-0.1574,  0.4091,  0.1209],
        [-0.1704,  0.3625,  0.1229],
        [-0.1834,  0.3925,  0.1343],
        [-0.1604,  0.3827,  0.1138],
        [-0.1532,  0.3779,  0.0993],
        [-0.1828,  0.3810,  0.1231],
        [-0.1757,  0.3668,  0.1075],
        [-0.1730,  0.3846,  0.1104],
        [-0.1652,  0.3669,  0.1115],
        [-0.1679,  0.3873,  0.1186],
        [-0.1652,  0.4018,  0.1103],
        [-0.1619,  0.3968,  0.0881],
        [-0.1843,  0.3640,  0.1126],
        [-0.1505,  0.3540,  0.0893],
        [-0.1666,  0.3755,  0.1015],
        [-0.1615,  0.3864,  0.1206],
        [-0.1561,  0.3585,  0.0969],
        [-0.1593,  0.3397,  0.0968],

Epoch number 0
 Current loss 0.9127746820449829

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[-0.2488,  0.4788,  0.1610],
        [-0.2206,  0.4870,  0.1390],
        [-0.2491,  0.5280,  0.1831],
        [-0.2497,  0.4946,  0.1658],
        [-0.2477,  0.4690,  0.1568],
        [-0.2395,  0.4818,  0.1629],
        [-0.2308,  0.4488,  0.1472],
        [-0.2279,  0.4940,  0.1582],
        [-0.2384,  0.4952,  0.1548],
        [-0.2416,  0.4701,  0.1535],
        [-0.2512,  0.4747,  0.1634],
        [-0.2396,  0.4815,  0.1678],
        [-0.2421,  0.4929,  0.1600],
        [-0.2091,  0.4653,  0.1386],
        [-0.2394,  0.4860,  0.1576],
        [-0.2549,  0.4924,  0.1705],
        [-0.2415,  0.4996,  0.1677],
        [-0.2388,  0.4681,  0.1444],
        [-0.2576,  0.4722,  0.1751],
        [-0.2466,  0.5131,  0.1686],
        [-0.2570,  0.5039,  0.1815],
        [-0.2355,  0.4869,  0.1612],
        [-0.2628,  0.4829,  0.1766],
        [-0.2423,  0.4627,  0.1618],

...

Epoch number 9
 Current loss 0.07294070720672607

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[ 1.6023, -5.1140, -0.3433],
        [-4.6720,  9.6953, -5.3182],
        [-2.4624, -5.5343,  6.9302],
        [-3.7064,  8.0658, -5.4340],
        [ 1.6778, -4.9829, -0.9538],
        [-4.5188,  7.7303, -3.0626],
        [-4.7053,  9.2297, -4.6115],
        [-3.4810,  6.2787, -3.7313],
        [-3.4298,  1.6231,  1.6220],
        [-1.5059, -2.8890,  3.0308],
        [-3.8267,  7.5439, -4.7147],
        [-3.4590,  6.3225, -3.7187],
        [-3.3026,  6.1321, -3.7805],
        [ 0.0255, -2.9246,  0.8005],
        [-3.6315,  5.8348, -2.8598],
        [-2.6635, -3.0646,  5.0404],
        [-3.3892,  4.3741, -1.5631],
        [-4.7125,  7.0603, -2.1588],
        [-4.8749,  8.1445, -3.0604],
        [-4.0096,  8.3324, -4.8708],
        [-4.4485,  6.5397, -1.7680],
        [ 1.3743, -5.8800,  0.4137],
        [-4.5192,  9.4231, -5.2301],
        [-2.5635,  4.7739, -3.9968]

Epoch number 9
 Current loss 0.02271922677755356

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[-2.5050, -5.1444,  6.6104],
        [-2.4470, -4.4205,  5.9158],
        [-0.8282,  1.7753, -3.0061],
        [ 1.4286, -4.2614, -1.0778],
        [-3.1483, -4.5264,  6.7390],
        [-3.5031,  6.0323, -3.1477],
        [-1.8684,  1.3534, -1.1213],
        [ 0.2382, -5.5744,  3.2907],
        [-3.5169,  6.1015, -3.1358],
        [-4.3848,  8.8102, -4.8373],
        [-1.9545, -4.9184,  5.8389],
        [-3.7751,  6.5872, -3.1987],
        [-3.5336,  7.4258, -5.0711],
        [-4.5470,  8.6419, -4.0716],
        [-1.9793, -5.5572,  6.4611],
        [-4.3417,  8.4792, -4.4275],
        [-4.9150,  7.6303, -2.2604],
        [-4.2784,  9.0799, -5.4561],
        [-4.9746,  8.7038, -3.5009],
        [-1.6852, -3.4256,  4.2960],
        [-2.3294, -5.3534,  6.5840],
        [-3.3977, -0.1510,  3.3213],
        [-4.1461,  7.0857, -3.0333],
        [-3.2672,  5.9836, -3.6242]

Epoch number 9
 Current loss 0.03261885792016983

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[-2.4826, -3.0298,  4.7787],
        [-5.0900,  8.7666, -3.4534],
        [-1.9219, -4.9454,  5.8581],
        [-5.6777,  8.6493, -2.3478],
        [-4.7897,  9.2169, -4.3921],
        [-4.0053,  6.4868, -2.6547],
        [-1.4510, -4.5082,  4.8007],
        [-4.1244,  6.6400, -2.4914],
        [-2.6689, -2.7763,  4.8155],
        [-4.0666,  8.3923, -5.1507],
        [-4.7658,  9.7216, -5.1526],
        [-2.3652, -5.1312,  6.4191],
        [-4.3616,  9.0820, -5.4454],
        [-1.9100, -5.3127,  6.1482],
        [-2.3227, -4.9466,  6.2701],
        [-4.5823,  8.3437, -3.7442],
        [-0.7355, -4.5737,  3.5716],
        [-5.5653,  8.4186, -2.2933],
        [-4.2298,  6.0594, -1.8925],
        [-1.8012, -4.9350,  5.7447],
        [ 1.6842, -5.5634,  0.1905],
        [-1.2628, -2.4964,  2.3202],
        [-3.8457,  5.6563, -2.0891],
        [-2.8983,  5.3519, -3.7260]

Epoch number 9
 Current loss 0.04039338231086731

inputs are
torch.Size([100, 128])
torch.Size([100, 128])
OUTPUT
tensor([[ 0.1538, -3.9674,  0.9364],
        [-3.8854,  6.0092, -2.4569],
        [-3.1324, -4.6526,  6.8262],
        [-4.7796,  9.7089, -5.1449],
        [-4.3849,  5.9286, -1.2634],
        [-4.7024,  9.3269, -4.8398],
        [-2.3852, -2.6508,  4.3870],
        [-1.6027, -4.9865,  5.4800],
        [-4.7068,  9.7252, -5.3470],
        [-4.7510,  9.1453, -4.5074],
        [-2.2108, -1.3189,  2.7937],
        [-4.8878,  9.3748, -4.4009],
        [-4.4990,  9.2118, -5.0611],
        [-5.1635,  8.1896, -2.5666],
        [ 1.1347, -6.1184,  1.4470],
        [-4.5199,  7.5564, -2.9183],
        [-4.6131,  8.6691, -4.2045],
        [-4.2515,  8.3381, -4.3790],
        [-4.7379,  8.5769, -3.8357],
        [-4.6386,  7.8482, -2.9940],
        [ 1.2721, -6.4567,  1.5102],
        [-3.2464,  6.0898, -3.9479],
        [-0.6661,  2.5262, -4.6240],
        [ 1.4591, -4.5495, -1.0760]

Epoch number 9
 Current loss 0.04700294882059097



In [20]:
def binary_accuracy(preds, y):
    """
    Returns accuracy per batch, i.e. if you get 8/10 right, this returns 0.8, NOT 8
    """
    #round predictions to the closest integer
    rounded_preds = torch.round(torch.sigmoid(preds)).float()
    print(rounded_preds.shape)
    correct = (rounded_preds == y).sum().item() #convert into float for division
    onf_matrix = confusion_matrix(rounded_preds, y)
    print(onf_matrix)
    acc = correct/y.shape[0]
    print(acc)
    return acc

In [82]:
def classification_accuracy(preds, y):
    _, predicted = torch.max(preds.data, 1)
    num_correct = (predicted == y).sum().item()
    print("num correct")
    print(num_correct)
    print(y.shape[0])
    conf_matrix = confusion_matrix(predicted, y)
    print(conf_matrix)
    return num_correct / y.shape[0]

In [80]:
def evaluate(model, iterator):
    epoch_loss = 0
    epoch_acc = 0
    
    model.eval()
    batch_num = 0
    accuracies = []
    i = 0
    with torch.no_grad():
        for i, data in enumerate(iterator,0):
            img0, img1 , label = data
            _, batch_size = img0.shape
            model.hidden1 = model.init_hidden(batch_size)
            model.hidden2 = model.init_hidden(batch_size)
            output = model(img0,img1)
            #accuracy = binary_accuracy(output.squeeze(), label.float())
            accuracy = classification_accuracy(output.squeeze(), label.long())
            accuracies.append(accuracy)
            i+=1
            print("current accuracy is")
            print(accuracy)
            if i % 20 == 0:
                print("cumulative accuracy")
                print(np.sum(accuracies) / i)
        print("FINAL")
        print(np.sum(accuracies) / i)

In [81]:
#most error comes from when it's actually 1 but we predict 0 (related but we predict unrelated)
evaluate(model, val_batch_it)


num correct
124
128
current accuracy is
0.96875
num correct
117
128
current accuracy is
0.9140625
num correct
115
128
current accuracy is
0.8984375
num correct
124
128
current accuracy is
0.96875
num correct
118
128
current accuracy is
0.921875
num correct
123
128
current accuracy is
0.9609375
num correct
113
128
current accuracy is
0.8828125
num correct
114
128
current accuracy is
0.890625
num correct
115
128
current accuracy is
0.8984375
num correct
116
128
current accuracy is
0.90625
num correct
120
128
current accuracy is
0.9375
num correct
125
128
current accuracy is
0.9765625
num correct
118
128
current accuracy is
0.921875
num correct
122
128
current accuracy is
0.953125
num correct
120
128
current accuracy is
0.9375
num correct
116
128
current accuracy is
0.90625
num correct
121
128
current accuracy is
0.9453125
num correct
119
128
current accuracy is
0.9296875
num correct
120
128
current accuracy is
0.9375
num correct
119
128
current accuracy is
0.9296875
cumulative accuracy
0

In [ ]:

# 0.8380412635833554 without 
# 0.8366860339915186 with extra layersa?!?!
# 0.8412300390935594 with only looking at 100 words
# 0.9252252849191624 with 100 and actual article lol, 10 epochs

# stance detection 0.9340277777777778